In [1]:
from sentence_transformers import SentenceTransformer, util
import pandas as pd
import re

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [2]:
# Target列を分割する関数
def split_target(target):
    # 指定された区切り文字で分割
    split_words = re.split(r'[,\n、・及びおよび又はまたは]+', target)
    # 空白文字を除外してリストとして返す
    return [word.strip() for word in split_words if word.strip()]

In [3]:
basedf = pd.read_csv('../ClinicalTrialCSV/JRCT20241202Cancer.csv', index_col=0)
basedf = basedf.dropna(subset=['試験等のフェーズ'])
# Target列を分割してTargetWord列を追加
basedf['TargetWord'] = basedf['Target'].apply(split_target)

In [4]:
# モデルのロード
model = SentenceTransformer("pkshatech/RoSEtta-base", trust_remote_code=True)

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/201 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/9.63k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/54.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/975 [00:00<?, ?B/s]

...

model.safetensors:   0%|          | 0.00/762M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.08k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/6.41M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/1.07k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

In [55]:
# クエリ
#query = "乳がん"
query = "神経膠腫"
threshold = 0.8
#threshold = 0.675
# クエリをベクトル化
query_vec = model.encode(query, convert_to_tensor=True)


In [56]:
# ターゲットリスト全体を処理
matched_indices = []
target_vecs_list = []
cosine_scores_list = []
for idx, target_words in enumerate(basedf['TargetWord']):
    # ターゲット内の各単語をベクトル化
    target_vecs = model.encode(target_words, convert_to_tensor=True)
    # コサイン類似度を計算
    cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()
    target_vecs_list.append(target_vecs)
    cosine_scores_list.append(cosine_scores)
    # 閾値を超えるか確認
    if (cosine_scores >= threshold).any():  # いずれかが閾値を超えている場合
        matched_indices.append(idx)

# 抽出
matched_df = basedf.iloc[matched_indices]
matched_df

JRCT ID       NCT No JapicCTI No  \
72   jRCT2051240141  NCT05580562         NaN   
103  jRCT2051240121  NCT06413706         NaN   
224  jRCT2031240090          NaN         NaN   
473  jRCT2051230069          NaN         NaN   
549  jRCT2031230007          NaN         NaN   
875  jRCT2031210299          NaN         NaN   
981  jRCT2031200153          NaN         NaN   

                                                 Title  \
72   新たに診断され放射線療法を完了したH3 K27M変異を有するびまん性神経膠腫の治療のためのO...   
103  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
224  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
473  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
549  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
875                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   
981                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験   

                       Target  \
72   H3 K27M 変異を有する初発びまん性神経膠腫   
103                    悪性神経膠腫   
224                    悪性神経膠腫   
473                      神経膠腫   
549               低悪性度神経膠腫、膵癌   
875                  再発悪性神経膠腫   
981                       膠芽腫   

                                              研究・治験の目的 試験等のフェーズ 試験の種類    無作為化  \
72   H3 K27M変異びまん性神経膠腫を有する被験者を対象に、放射線療法後に投与されたONC20...        3   NaN  無作為化比較   
103  放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN  無作為化比較   
224  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis（N4-methyl...        3   NaN  無作為化比較   
473  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...        1   NaN     単一群   
549  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫（コホート A...        2   NaN     単一群   
875  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN     単一群   
981  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3   NaN  無作為化比較   

      盲検化  ...            purpose  \
72   二重盲検  ...  treatment purpose   
103   非盲検  ...  treatment purpose   
224   非盲検  ...  treatment purpose   
473   非盲検  ...  treatment purpose   
549   非盲検  ...  treatment purpose   
875   非盲検  ...  treatment purpose   
981  二重盲検  ...  treatment purpose   

                                    Inclusion Criteria  \
72   1. Able to understand the study procedures and...   
103  Subjects required to meet all the folloiwng cr...   
224  1) Histologically diagnosed as high grade glio...   
473  <Cohort 1>\r\n All of the following items shal...   
549  Inclusion criteria for both cohort A and B\r\n...   
875  1.\tEstimated life expectancy >= 3 months\r\n2...   
981  (1) 18 years old or older and 75 years old or ...   

                                    Exclusion Criteria     Age Minimum  \
72   1. Primary spinal tumor.\r\n2. Diffuse intrins...        No limit   
103  Patients who meets any of the following criter...        No limit   
224  1) Have a history or merger of other malignanc...  18age old over   
473  <Common to Cohort 1 and Cohort 2>\r\n1) Active...  18age old over   
549  1) Active double primary cancer (but not (1)-(...  12age old over   
875  1.\tPrior therapy with bevacizumab or other an...  18age old over   
981  (1) Systemic administration of corticosteroids...  18age old over   

         Age Maximum Gender Discontinuation Criteria  \
72          No limit    NaN                      NaN   
103    21age old not    NaN                      NaN   
224  75age old under   Both                      NaN   
473         No limit   Both                      NaN   
549         No limit   Both                      NaN   
875         No limit   Both                      NaN   
981  75age old under   Both                      NaN   

                                               Keyword  \
72                                                 NaN   
103                                                NaN   
224  glioblastoma, grade3/4 astrocytoma, grade3 oli...   
473                                                NaN   
549  BRAF fusion gene, BRAF rearrangement, low-grad...   
875                                                NaN   
981                                   

In [57]:
# 全データのターゲット列をベクトル化
target_list = basedf['Target'].tolist()
target_vecs = model.encode(target_list, convert_to_tensor=True)
# コサイン類似度を計算
cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()

In [58]:
matched_indices_d = (cosine_scores >= threshold).nonzero().tolist()
# 入れ子リストをフラットなリストに変換
flat_indices_d = [idx[0] for idx in matched_indices_d]

# 抽出
matched_df_d = basedf.iloc[flat_indices_d]
matched_df_d


JRCT ID       NCT No JapicCTI No  \
103  jRCT2051240121  NCT06413706         NaN   
224  jRCT2031240090          NaN         NaN   
473  jRCT2051230069          NaN         NaN   
875  jRCT2031210299          NaN         NaN   
981  jRCT2031200153          NaN         NaN   

                                                 Title    Target  \
103  放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...    悪性神経膠腫   
224  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...    悪性神経膠腫   
473  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...      神経膠腫   
875                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験  再発悪性神経膠腫   
981                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験       膠芽腫   

                                              研究・治験の目的 試験等のフェーズ 試験の種類    無作為化  \
103  放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN  無作為化比較   
224  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis（N4-methyl...        3   NaN  無作為化比較   
473  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...        1   NaN     単一群   
875  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN     単一群   
981  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3   NaN  無作為化比較   

      盲検化  ...            purpose  \
103   非盲検  ...  treatment purpose   
224   非盲検  ...  treatment purpose   
473   非盲検  ...  treatment purpose   
875   非盲検  ...  treatment purpose   
981  二重盲検  ...  treatment purpose   

                                    Inclusion Criteria  \
103  Subjects required to meet all the folloiwng cr...   
224  1) Histologically diagnosed as high grade glio...   
473  <Cohort 1>\r\n All of the following items shal...   
875  1.\tEstimated life expectancy >= 3 months\r\n2...   
981  (1) 18 years old or older and 75 years old or ...   

                                    Exclusion Criteria     Age Minimum  \
103  Patients who meets any of the following criter...        No limit   
224  1) Have a history or merger of other malignanc...  18age old over   
473  <Common to Cohort 1 and Cohort 2>\r\n1) Active...  18age old over   
875  1.\tPrior therapy with bevacizumab or other an...  18age old over   
981  (1) Systemic administration of corticosteroids...  18age old over   

         Age Maximum Gender Discontinuation Criteria  \
103    21age old not    NaN                      NaN   
224  75age old under   Both                      NaN   
473         No limit   Both                      NaN   
875         No limit   Both                      NaN   
981  75age old under   Both                      NaN   

                                               Keyword  \
103                                                NaN   
224  glioblastoma, grade3/4 astrocytoma, grade3 oli...   
473                                                NaN   
875                                                NaN   
981                                                NaN   

                                       Intervention(s)  TargetWord  
103  Drug: Abemaciclib\r\nAdministered orally\r\nOt...    [悪性神経膠腫]  
224  Group A: BPC Therapy\r\nDepending on the patie...    [悪性神経膠腫]  
473  <cohort1>\r\nLomustine 130 mg/m2 orally every ...      [神経膠腫]  
875  Patients will receive DSP-0390 orally once dai...  [再発悪性神経膠腫]  
981  Inject the investigational drug (Cellm-001 or ...       [膠芽腫]  

[5 rows x 39 columns]